In [1]:
latest_gameweek = 10

In [2]:
import pandas as pd
import numpy as np
from pathlib import Path
from pulp import LpMaximize, LpProblem, LpStatus, lpSum, LpVariable

# Solver

In [3]:
def optimize(df, max_price, expected_column, captain_double_points=True):
    '''Function for solving the optimization problem.'''    
    # PRELIMINARIES

    # Create the model
    model = LpProblem(name="FPL", sense=LpMaximize)    
    variables = [LpVariable(name=f'{ix}', cat='Binary') for ix in df.index]
    captaincy_variables = [LpVariable(name=f'cap_{ix}', cat='Binary') for ix in df.index]
    prices = [df.loc[ix,'price'] for ix in df.index]
    # measure of player quality
    expected_points = [df.loc[ix,expected_column] for ix in df.index]
    goalkeepers = [1.0 if df.loc[ix,'position']=='GK' else 0.0 for ix in df.index]
    defenders = [1.0 if df.loc[ix,'position']=='DEF' else 0.0 for ix in df.index]
    midfielders = [1.0 if df.loc[ix,'position']=='MID' else 0.0 for ix in df.index]
    forwards = [1.0 if df.loc[ix,'position']=='FWD' else 0.0 for ix in df.index]
    teams = []
    for team in df['team'].unique():
        teams.append( [1.0 if df.loc[ix,'team']==team else 0.0 for ix in df.index] )

    # CONSTRAINTS

    # select 11 players
    model += lpSum(variables) == 11
    # select 1 captain
    model += lpSum(captaincy_variables) == 1
    # captain must be one of the 11 players in the team
    for i in range(0,len(variables)):
        model += captaincy_variables[i] <= variables[i]
    # set maximum price for starting 11
    model += np.dot(prices,variables) <= max_price
    # only 1 goalkeeper
    model += np.dot(goalkeepers,variables) == 1
    # at least 3 defenders
    model += np.dot(defenders,variables) >= 3
    # at most 5 defenders
    model += np.dot(defenders,variables) <= 5
    # at most 5 midfielders
    model += np.dot(midfielders,variables) <= 5
    # at least 1 forward
    model += np.dot(forwards,variables) >= 1
    # at most 3 forwards
    model += np.dot(forwards,variables) <= 3
    # max 3 players from any given team
    for team in teams:
        model += np.dot(team,variables) <= 3

    # OBJECTIVE
    if captain_double_points:
        # the second part doubles the captain's points
        model += np.dot(expected_points,variables) + np.dot(expected_points,captaincy_variables)
    else:
        model += np.dot(expected_points,variables)

    # SOLVE OPTIMIZATION

    status = model.solve()
    print(f'Status: {LpStatus[model.status]}')
    #print(f'Mean total points per gameweek: {model.objective.value()}')

    players = [str(var) for var in model.variables() if var.value()==1]
    captain = [player for player in players if 'cap' in player]
    captain = int(captain[0].replace('cap_', ''))
    players = [int(player) for player in players if 'cap' not in player]
    dream_team = df.loc[players]
    cost = (dream_team['price']).sum()
    exp_points = dream_team[expected_column].sum() + df.loc[captain, expected_column]
    print(f'Cost: {cost}')
    print(f'Expected points per week: {exp_points}')
    
    display(dream_team[['position','name', 'team', 'price', expected_column]].sort_values('position'))
    
    return players

# Data

In [4]:
path = Path(f'../data/predictions/gameweek{latest_gameweek}.csv')
projections = pd.read_csv(path, index_col=0)
projections.head(5)

name  element_type  home  corners_and_indirect_freekicks_order  \
0  Aaron Cresswell             2     0                                   NaN   
1  Aaron Cresswell             2     1                                   NaN   
2  Aaron Cresswell             2     0                                   NaN   
3  Aaron Cresswell             2     1                                   NaN   
4  Aaron Cresswell             2     0                                   NaN   

   creativity_rank  direct_freekicks_order  ict_index_rank  influence_rank  \
0              305                     NaN             383             387   
1              305                     NaN             383             387   
2              305                     NaN             383             387   
3              305                     NaN             383             387   
4              305                     NaN             383             387   

   minutes  now_cost  ...  gameweek_xG_expanding_per90  \
0       84        42  ...                     0.024176   
1       84        42  ...                     0.024176   
2       84        42  ...                     0.024176   
3       84        42  ...                     0.024176   
4       84        42  ...                     0.024176   

   gameweek_xA_expanding_per90  gameweek_xGA_expanding_per90  \
0                     0.146596                      1.378362   
1                     0.146596                      1.378362   
2                     0.146596                      1.378362   
3                     0.146596                      1.378362   
4                     0.146596                      1.378362   

   gameweek_xPoints_expanding_per90  xG_overperformance  team_name  \
0                          3.670647            1.950078   West Ham   
1                          3.670647            1.950078   West Ham   
2                          3.670647            1.950078   West Ham   
3                          3.670647            1.950078   West Ham   
4                          3.670647            1.950078   West Ham   

       opponent_team                  date  gameweek  expected_points  
0          Brentford  2023-11-04T15:00:00Z        11         2.333516  
1  Nottingham Forest  2023-11-12T14:00:00Z        12         3.267850  
2            Burnley  2023-11-25T15:00:00Z        13         3.098982  
3     Crystal Palace  2023-12-03T14:00:00Z        14         3.168207  
4          Tottenham  2023-12-07T20:15:00Z        15         2.370271  

[5 rows x 113 columns]

In [5]:
# decay for future projected points to model uncertainty increasing over time
decay_coeff = 0.875
projections['expected_points_with_decay'] = ( projections['expected_points']*decay_coeff
                                              **(projections['gameweek']-1) )
projections.head(5)

name  element_type  home  corners_and_indirect_freekicks_order  \
0  Aaron Cresswell             2     0                                   NaN   
1  Aaron Cresswell             2     1                                   NaN   
2  Aaron Cresswell             2     0                                   NaN   
3  Aaron Cresswell             2     1                                   NaN   
4  Aaron Cresswell             2     0                                   NaN   

   creativity_rank  direct_freekicks_order  ict_index_rank  influence_rank  \
0              305                     NaN             383             387   
1              305                     NaN             383             387   
2              305                     NaN             383             387   
3              305                     NaN             383             387   
4              305                     NaN             383             387   

   minutes  now_cost  ...  gameweek_xA_expanding_per90  \
0       84        42  ...                     0.146596   
1       84        42  ...                     0.146596   
2       84        42  ...                     0.146596   
3       84        42  ...                     0.146596   
4       84        42  ...                     0.146596   

   gameweek_xGA_expanding_per90  gameweek_xPoints_expanding_per90  \
0                      1.378362                          3.670647   
1                      1.378362                          3.670647   
2                      1.378362                          3.670647   
3                      1.378362                          3.670647   
4                      1.378362                          3.670647   

   xG_overperformance  team_name      opponent_team                  date  \
0            1.950078   West Ham          Brentford  2023-11-04T15:00:00Z   
1            1.950078   West Ham  Nottingham Forest  2023-11-12T14:00:00Z   
2            1.950078   West Ham            Burnley  2023-11-25T15:00:00Z   
3            1.950078   West Ham     Crystal Palace  2023-12-03T14:00:00Z   
4            1.950078   West Ham          Tottenham  2023-12-07T20:15:00Z   

   gameweek  expected_points  expected_points_with_decay  
0        11         2.333516                    0.613891  
1        12         3.267850                    0.752230  
2        13         3.098982                    0.624188  
3        14         3.168207                    0.558365  
4        15         2.370271                    0.365520  

[5 rows x 114 columns]

In [6]:
my_gameweeks = np.arange(latest_gameweek+1, latest_gameweek+11, 1)
#my_gameweeks = np.arange(latest_gameweek+1, latest_gameweek+4, 1)
#my_gameweeks = np.arange(latest_gameweek+2, latest_gameweek+12, 1)
df = projections[projections['gameweek'].isin(my_gameweeks)].groupby(by=['name', 'team_name']).sum()\
                                                        [['expected_points','expected_points_with_decay']]
df['number_of_games'] = (
    projections[projections['gameweek']
    .isin(my_gameweeks)]
    .groupby(['name', 'team_name'])
    .count()['element_type']
)

df = df.reset_index()

df['position'] = [projections.loc[projections['name']==name, 'element_type'].values[0] for name in df['name']]
position_dict={1:'GK', 2:'DEF', 3:'MID', 4:'FWD'}
df['position'] = df['position'].map(position_dict)
df['position'] = pd.Categorical(df['position'], ['GK','DEF','MID','FWD'])

df['price'] = [projections.loc[projections['name']==name, 'now_cost'].values[0] for name in df['name']]
df['price'] = df['price'] / 10.0

df['team'] = [projections.loc[projections['name']==name, 'team_name'].values[0] for name in df['name']]

df

name       team_name  expected_points  \
0             Aaron Cresswell        West Ham        27.951781   
1                Aaron Hickey       Brentford        21.796843   
2              Aaron Ramsdale         Arsenal        35.942762   
3                Aaron Ramsey         Burnley        19.541430   
4           Aaron Wan-Bissaka  Manchester Utd        29.618709   
..                        ...             ...              ...   
455               Yoane Wissa       Brentford        35.828415   
456           Youri Tielemans     Aston Villa        26.420029   
457  Youssef Ramalho Chermiti         Everton        14.912815   
458             Yves Bissouma       Tottenham        22.159430   
459              Zeki Amdouni         Burnley        22.888609   

     expected_points_with_decay  number_of_games position  price  \
0                      4.388729               10      DEF    4.2   
1                      3.423306                9      DEF    4.5   
2                      5.530606               10       GK    5.0   
3                      3.063098               10      MID    5.0   
4                      4.682982               10      DEF    4.6   
..                          ...              ...      ...    ...   
455                    5.648388                9      FWD    5.9   
456                    4.109693               10      MID    5.7   
457                    2.320378               10      FWD    4.9   
458                    3.413036               10      MID    5.0   
459                    3.590575               10      FWD    5.4   

               team  
0          West Ham  
1         Brentford  
2           Arsenal  
3           Burnley  
4    Manchester Utd  
..              ...  
455       Brentford  
456     Aston Villa  
457         Everton  
458       Tottenham  
459         Burnley  

[460 rows x 8 columns]

# Optimization

In [7]:
team_value = 101.
money_in_the_bank = 1.1
allowed_bench_value = 17.5
max_price = team_value + money_in_the_bank - allowed_bench_value

In [8]:
ban = []

# ban some cheap keepers in good teams who don't actually play
cheap_keepers = ['Robin Olsen', 'Jason Steele']
cheap_keepers_ix = df[df['name'].isin(cheap_keepers)].index
ban = ban + list(cheap_keepers_ix)

# ban given outfield players
ban_field = ['Kevin De Bruyne', 'Andrew Robertson', 'Pervis Estupiñán', 'Sven Botman', 'Luke Shaw', 'Pascal Groß']
ban_field_ix = df[df['name'].isin(ban_field)].index
ban = ban + list(ban_field_ix)

my_df = df.drop(ban).copy()

In [9]:
players = optimize(my_df, max_price, 'expected_points_with_decay')

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/37a1dd20e738401b85b3de21754e9b09-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/37a1dd20e738401b85b3de21754e9b09-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 486 COLUMNS
At line 6575 RHS
At line 7057 BOUNDS
At line 7962 ENDATA
Problem MODEL has 481 rows, 904 columns and 3376 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 93.952 - 0.00 seconds
Cgl0004I processed model has 479 rows, 904 columns (904 integer (904 of which binary)) and 3164 elements
Cbc0038I Initial state - 2 integers unsatisfied sum - 0.214286
Cbc0038I Solution found of -93.802

position                    name            team  price  \
20        GK   Alisson Ramses Becker       Liverpool    5.6   
212      DEF        Joachim Andersen  Crystal Palace    5.0   
253      DEF         Kieran Trippier   Newcastle Utd    7.0   
307      DEF              Matty Cash     Aston Villa    5.2   
434      DEF  Trent Alexander-Arnold       Liverpool    7.9   
162      MID           Heung-Min Son       Tottenham    9.6   
202      MID            Jarrod Bowen        West Ham    7.4   
322      MID           Mohamed Salah       Liverpool   12.9   
68       MID            Bryan Mbeumo       Brentford    6.7   
69       MID             Bukayo Saka         Arsenal    8.6   
353      FWD           Ollie Watkins     Aston Villa    8.4   

     expected_points_with_decay  
20                     6.144823  
212                    5.582605  
253                    7.230377  
307                    5.901607  
434                    7.450584  
162                    9.037080  
202                    7.633065  
322                   10.014471  
68                     7.817236  
69                     8.783742  
353                    8.192552

In [10]:
sigma=0.5
simulation_rounds = 500
next_gameweek=latest_gameweek+1

ban = []

# ban some cheap keepers in good teams who don't actually play
cheap_keepers = ['Robin Olsen']
cheap_keepers_ix = df[df['name'].isin(cheap_keepers)].index
ban = ban + list(cheap_keepers_ix)

# ban given outfield players
ban_field = ['Kevin De Bruyne', 'Andrew Robertson']
ban_field_ix = df[df['name'].isin(ban_field)].index
ban = ban + list(ban_field_ix)

results = []
for i in range(simulation_rounds):
 
    # add random noise to expected points (a fixed offset for every projection of any given player)
    projections['expected_points_with_noise'] = (projections
    .groupby('name')
    .apply(lambda x: x['expected_points']+np.random.normal(0,sigma))
    .reset_index()
    .sort_values('level_1')
    ['expected_points']
    .values
    )

    # decay
    projections['expected_points_with_noise_with_decay'] = ( projections['expected_points_with_noise']*decay_coeff
                                              **(projections['gameweek']-next_gameweek) )

    df['expected_points_with_noise_with_decay'] = projections[projections['gameweek'].isin(my_gameweeks)].groupby(by=['name', 'team_name']).sum()\
                                                            ['expected_points_with_noise_with_decay'].values

    my_df = df.drop(ban).copy()
    
    players = optimize(my_df, max_price, 'expected_points_with_noise_with_decay')

    results.append(players)
    

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/80c38e7c3c274387927891aa7af6f99d-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/80c38e7c3c274387927891aa7af6f99d-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 491 COLUMNS
At line 6648 RHS
At line 7135 BOUNDS
At line 8050 ENDATA
Problem MODEL has 486 rows, 914 columns and 3414 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 386.591 - 0.00 seconds
Cgl0004I processed model has 484 rows, 914 columns (914 integer (914 of which binary)) and 3199 elements
Cbc0038I Initial state - 2 integers unsatisfied sum - 0.947368
Cbc0038I Pass   1: suminf.    0.3

position                       name             team  price  \
125       GK  Ederson Santana de Moraes  Manchester City    5.5   
412      DEF                Sven Botman    Newcastle Utd    4.7   
434      DEF     Trent Alexander-Arnold        Liverpool    7.9   
47       DEF                Axel Disasi          Chelsea    5.1   
162      MID              Heung-Min Son        Tottenham    9.6   
192      MID             James Maddison        Tottenham    8.1   
202      MID               Jarrod Bowen         West Ham    7.4   
322      MID              Mohamed Salah        Liverpool   12.9   
69       MID                Bukayo Saka          Arsenal    8.6   
17       FWD             Alexander Isak    Newcastle Utd    7.5   
240      FWD             Julián Álvarez  Manchester City    7.2   

     expected_points_with_noise_with_decay  
125                              27.216662  
412                              27.719643  
434                              31.894105  
47                               26.196982  
162                              37.061109  
192                              30.153203  
202                              28.598391  
322                              41.347014  
69                               33.747373  
17                               30.441138  
240                              30.293581

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/fd022a9fcc7e4c87b7105c57896613e5-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/fd022a9fcc7e4c87b7105c57896613e5-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 491 COLUMNS
At line 6648 RHS
At line 7135 BOUNDS
At line 8050 ENDATA
Problem MODEL has 486 rows, 914 columns and 3414 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 369.282 - 0.00 seconds
Cgl0004I processed model has 484 rows, 914 columns (914 integer (914 of which binary)) and 3199 elements
Cbc0038I Initial state - 0 integers unsatisfied sum - 3.44169e-15
Cbc0038I Solution found of -36

position                    name           team  price  \
107       GK       David Raya Martin        Arsenal    4.8   
365      DEF        Pervis Estupiñán       Brighton    5.3   
434      DEF  Trent Alexander-Arnold      Liverpool    7.9   
441      DEF         Virgil van Dijk      Liverpool    6.1   
162      MID           Heung-Min Son      Tottenham    9.6   
192      MID          James Maddison      Tottenham    8.1   
202      MID            Jarrod Bowen       West Ham    7.4   
322      MID           Mohamed Salah      Liverpool   12.9   
360      MID             Pascal Groß       Brighton    6.3   
353      FWD           Ollie Watkins    Aston Villa    8.4   
72       FWD           Callum Wilson  Newcastle Utd    7.8   

     expected_points_with_noise_with_decay  
107                              26.988154  
365                              25.597545  
434                              27.440925  
441                              27.833111  
162                              32.061544  
192                              31.456778  
202                              30.877545  
322                              38.548215  
360                              30.540451  
353                              32.847131  
72                               26.542200

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/69b53e4397224e59932c7250408caaf1-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/69b53e4397224e59932c7250408caaf1-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 491 COLUMNS
At line 6648 RHS
At line 7135 BOUNDS
At line 8050 ENDATA
Problem MODEL has 486 rows, 914 columns and 3414 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 378.78 - 0.00 seconds
Cgl0004I processed model has 484 rows, 914 columns (914 integer (914 of which binary)) and 3199 elements
Cbc0038I Initial state - 2 integers unsatisfied sum - 0.818182
Cbc0038I Pass   1: suminf.    0.31

...

position                    name            team  price  \
339       GK               Nick Pope   Newcastle Utd    5.5   
277      DEF               Luke Shaw  Manchester Utd    5.5   
434      DEF  Trent Alexander-Arnold       Liverpool    7.9   
56       DEF          Benjamin White         Arsenal    5.7   
162      MID           Heung-Min Son       Tottenham    9.6   
198      MID       James Ward-Prowse        West Ham    6.2   
247      MID            Kaoru Mitoma        Brighton    6.5   
322      MID           Mohamed Salah       Liverpool   12.9   
69       MID             Bukayo Saka         Arsenal    8.6   
353      FWD           Ollie Watkins     Aston Villa    8.4   
72       FWD           Callum Wilson   Newcastle Utd    7.8   

     expected_points_with_noise_with_decay  
339                              25.845258  
277                              29.884047  
434                              28.598504  
56                               26.506844  
162                              31.928776  
198                              29.428668  
247                              29.601660  
322                              41.630453  
69                               35.346811  
353                              29.390215  
72                               27.786587

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/f9965d773b2e4bf7b7ac9dff7a58829a-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/f9965d773b2e4bf7b7ac9dff7a58829a-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 491 COLUMNS
At line 6648 RHS
At line 7135 BOUNDS
At line 8050 ENDATA
Problem MODEL has 486 rows, 914 columns and 3414 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 350.452 - 0.00 seconds
Cgl0004I processed model has 484 rows, 914 columns (914 integer (914 of which binary)) and 3199 elements
Cbc0038I Initial state - 0 integers unsatisfied sum - 2.22045e-16
Cbc0038I Solution found of -35

position                    name            team  price  \
20        GK   Alisson Ramses Becker       Liverpool    5.6   
195      DEF         James Tarkowski         Everton    4.4   
307      DEF              Matty Cash     Aston Villa    5.2   
434      DEF  Trent Alexander-Arnold       Liverpool    7.9   
162      MID           Heung-Min Son       Tottenham    9.6   
192      MID          James Maddison       Tottenham    8.1   
322      MID           Mohamed Salah       Liverpool   12.9   
65       MID  Bruno Borges Fernandes  Manchester Utd    8.3   
68       MID            Bryan Mbeumo       Brentford    6.7   
17       FWD          Alexander Isak   Newcastle Utd    7.5   
353      FWD           Ollie Watkins     Aston Villa    8.4   

     expected_points_with_noise_with_decay  
20                               26.685416  
195                              24.980979  
307                              25.249405  
434                              26.692395  
162                              30.802853  
192                              30.645626  
322                              32.215990  
65                               30.662545  
68                               30.209002  
17                               27.981375  
353                              32.110302

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/998edd3b7ac9452386958ec7be742a20-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/998edd3b7ac9452386958ec7be742a20-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 491 COLUMNS
At line 6648 RHS
At line 7135 BOUNDS
At line 8050 ENDATA
Problem MODEL has 486 rows, 914 columns and 3414 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 371.915 - 0.00 seconds
Cgl0004I processed model has 484 rows, 914 columns (914 integer (914 of which binary)) and 3199 elements
Cbc0038I Initial state - 0 integers unsatisfied sum - 0
Cbc0038I Solution found of -371.915
Cbc0

position                   name            team  price  \
20        GK  Alisson Ramses Becker       Liverpool    5.6   
266      DEF             Lewis Dunk        Brighton    5.0   
277      DEF              Luke Shaw  Manchester Utd    5.5   
307      DEF             Matty Cash     Aston Villa    5.2   
162      MID          Heung-Min Son       Tottenham    9.6   
192      MID         James Maddison       Tottenham    8.1   
322      MID          Mohamed Salah       Liverpool   12.9   
360      MID            Pascal Groß        Brighton    6.3   
69       MID            Bukayo Saka         Arsenal    8.6   
17       FWD         Alexander Isak   Newcastle Utd    7.5   
353      FWD          Ollie Watkins     Aston Villa    8.4   

     expected_points_with_noise_with_decay  
20                               27.056110  
266                              24.842513  
277                              29.790899  
307                              27.707498  
162                              36.196298  
192                              31.944529  
322                              35.484021  
360                              29.122303  
69                               33.268707  
17                               29.084539  
353                              31.221289

In [11]:
my_df['dream_team_appearances'] = [sum(team.count(player_id) / simulation_rounds for team in results) for player_id in my_df.index]

In [12]:
print('Most appearances, all players:')
display(my_df
        .drop(['team', 'expected_points_with_noise_with_decay'], axis=1)
        .sort_values(by='dream_team_appearances', ascending=False)
        .head(20))

Most appearances, all players:


name        team_name  expected_points  \
322           Mohamed Salah        Liverpool        63.742442   
353           Ollie Watkins      Aston Villa        52.907381   
69              Bukayo Saka          Arsenal        56.958652   
162           Heung-Min Son        Tottenham        58.254488   
434  Trent Alexander-Arnold        Liverpool        47.164820   
253         Kieran Trippier    Newcastle Utd        46.799988   
68             Bryan Mbeumo        Brentford        49.196225   
192          James Maddison        Tottenham        50.971203   
202            Jarrod Bowen         West Ham        49.134280   
72            Callum Wilson    Newcastle Utd        45.361440   
17           Alexander Isak    Newcastle Utd        42.881278   
20    Alisson Ramses Becker        Liverpool        38.944629   
365        Pervis Estupiñán         Brighton        37.730173   
307              Matty Cash      Aston Villa        37.836918   
360             Pascal Groß         Brighton        43.654466   
294         Martin Ødegaard          Arsenal        47.226310   
240          Julián Álvarez  Manchester City        40.480384   
247            Kaoru Mitoma         Brighton        44.091225   
104    Darwin Núñez Ribeiro        Liverpool        41.565175   
277               Luke Shaw   Manchester Utd        37.362101   

     expected_points_with_decay  number_of_games position  price  \
322                   10.014471               10      MID   12.9   
353                    8.192552               10      FWD    8.4   
69                     8.783742               10      MID    8.6   
162                    9.037080               10      MID    9.6   
434                    7.450584               10      DEF    7.9   
253                    7.230377               10      DEF    7.0   
68                     7.817236                9      MID    6.7   
192                    7.859116               10      MID    8.1   
202                    7.633065               10      MID    7.4   
72                     6.977332               10      FWD    7.8   
17                     6.632418               10      FWD    7.5   
20                     6.144823               10       GK    5.6   
365                    5.947128               10      DEF    5.3   
307                    5.901607               10      DEF    5.2   
360                    6.880755               10      MID    6.3   
294                    7.276201               10      MID    8.5   
240                    6.412950                9      FWD    7.2   
247                    6.942313               10      MID    6.5   
104                    6.516042               10      FWD    7.5   
277                    5.888240               10      DEF    5.5   

     dream_team_appearances  
322                   0.954  
353                   0.864  
69                    0.848  
162                   0.836  
434                   0.718  
253                   0.654  
68                    0.482  
192                   0.422  
202                   0.364  
72                    0.348  
17                    0.182  
20                    0.174  
365                   0.166  
307                   0.150  
360                   0.146  
294                   0.146  
240                   0.142  
247                   0.140  
104                   0.132  
277                   0.126

In [13]:
print('GOALKEEPERS')
display(my_df
        .drop(['team', 'expected_points_with_noise_with_decay'], axis=1)
        [my_df['position']=='GK']
        .sort_values(by='dream_team_appearances', ascending=False)
        .head(20))

GOALKEEPERS


name          team_name  expected_points  \
20       Alisson Ramses Becker          Liverpool        38.944629   
339                  Nick Pope      Newcastle Utd        37.565059   
107          David Raya Martin            Arsenal        36.458515   
31                 André Onana     Manchester Utd        35.000559   
125  Ederson Santana de Moraes    Manchester City        36.535396   
2               Aaron Ramsdale            Arsenal        35.942762   
394              Sam Johnstone     Crystal Palace        33.713088   
203               Jason Steele           Brighton        34.673225   
58                  Bernd Leno             Fulham        34.165072   
21             Alphonse Areola           West Ham        33.082836   
151          Guglielmo Vicario          Tottenham        35.163672   
423           Thomas Strakosha          Brentford        32.750666   
233        José Malheiro de Sá             Wolves        32.792491   
345       Norberto Murara Neto        Bournemouth        32.411982   
382             Robert Sánchez            Chelsea        35.315750   
228            Jordan Pickford            Everton        31.433055   
132   Emiliano Martínez Romero        Aston Villa        30.441859   
171                 Ionuț Radu        Bournemouth        32.801290   
411       Stefan Ortega Moreno    Manchester City        28.774623   
306                Matt Turner  Nottingham Forest        28.584738   

     expected_points_with_decay  number_of_games position  price  \
20                     6.144823               10       GK    5.6   
339                    5.770927               10       GK    5.5   
107                    5.613807               10       GK    4.8   
31                     5.528932               10       GK    4.8   
125                    5.743354                9       GK    5.5   
2                      5.530606               10       GK    5.0   
394                    5.413986               10       GK    4.6   
203                    5.448232               10       GK    4.3   
58                     5.255307               10       GK    4.7   
21                     5.185922               10       GK    4.3   
151                    5.410598               10       GK    5.2   
423                    5.142290                9       GK    3.9   
233                    5.208070               10       GK    5.0   
345                    4.879968               10       GK    4.5   
382                    5.163341               10       GK    4.6   
228                    4.900943               10       GK    4.4   
132                    4.749789               10       GK    4.9   
171                    4.925502               10       GK    4.4   
411                    4.528263                9       GK    3.9   
306                    4.431841               10       GK    4.1   

     dream_team_appearances  
20                    0.174  
339                   0.092  
107                   0.088  
31                    0.082  
125                   0.078  
2                     0.074  
394                   0.064  
203                   0.060  
58                    0.054  
21                    0.050  
151                   0.048  
423                   0.032  
233                   0.028  
345                   0.020  
382                   0.016  
228                   0.014  
132                   0.008  
171                   0.006  
411                   0.006  
306                   0.002

In [14]:
print('DEFENDERS')
display(my_df
        .drop(['team', 'expected_points_with_noise_with_decay'], axis=1)
        [my_df['position']=='DEF']
        .sort_values(by='dream_team_appearances', ascending=False)
        .head(20))

DEFENDERS


name        team_name  expected_points  \
434        Trent Alexander-Arnold        Liverpool        47.164820   
253               Kieran Trippier    Newcastle Utd        46.799988   
365              Pervis Estupiñán         Brighton        37.730173   
307                    Matty Cash      Aston Villa        37.836918   
277                     Luke Shaw   Manchester Utd        37.362101   
441               Virgil van Dijk        Liverpool        37.321008   
56                 Benjamin White          Arsenal        36.763660   
212              Joachim Andersen   Crystal Palace        34.824283   
449                William Saliba          Arsenal        36.022584   
412                   Sven Botman    Newcastle Utd        35.746759   
271                   Lucas Digne      Aston Villa        34.062840   
98                       Dan Burn    Newcastle Utd        34.665834   
238                Joško Gvardiol  Manchester City        34.690283   
288                    Marc Guéhi   Crystal Palace        33.045005   
266                    Lewis Dunk         Brighton        34.880160   
363                   Pedro Porro        Tottenham        34.687745   
50                   Ben Chilwell          Chelsea        36.278446   
137              Ezri Konsa Ngoyo      Aston Villa        33.539753   
147  Gabriel dos Santos Magalhães          Arsenal        34.269005   
138                  Fabian Schär    Newcastle Utd        34.619348   

     expected_points_with_decay  number_of_games position  price  \
434                    7.450584               10      DEF    7.9   
253                    7.230377               10      DEF    7.0   
365                    5.947128               10      DEF    5.3   
307                    5.901607               10      DEF    5.2   
277                    5.888240               10      DEF    5.5   
441                    5.872544               10      DEF    6.1   
56                     5.655113               10      DEF    5.7   
212                    5.582605               10      DEF    5.0   
449                    5.542372               10      DEF    5.2   
412                    5.500280               10      DEF    4.7   
271                    5.307114               10      DEF    4.7   
98                     5.328738               10      DEF    4.7   
238                    5.460638                9      DEF    5.0   
288                    5.310404               10      DEF    4.6   
266                    5.502054               10      DEF    5.0   
363                    5.341212               10      DEF    5.2   
50                     5.300494               10      DEF    5.6   
137                    5.235107               10      DEF    4.5   
147                    5.270079               10      DEF    4.7   
138                    5.320706               10      DEF    5.2   

     dream_team_appearances  
434                   0.718  
253                   0.654  
365                   0.166  
307                   0.150  
277                   0.126  
441                   0.114  
56                    0.100  
212                   0.094  
449                   0.084  
412                   0.072  
271                   0.070  
98                    0.064  
238                   0.058  
288                   0.058  
266                   0.056  
363                   0.050  
50                    0.046  
137                   0.038  
147                   0.038  
138                   0.028

In [15]:
print('MIDFIELDERS')
display(my_df
        .drop(['team', 'expected_points_with_noise_with_decay'], axis=1)
        [my_df['position']=='MID']
        .sort_values(by='dream_team_appearances', ascending=False)
        .head(20))

MIDFIELDERS


name        team_name  expected_points  \
322                 Mohamed Salah        Liverpool        63.742442   
69                    Bukayo Saka          Arsenal        56.958652   
162                 Heung-Min Son        Tottenham        58.254488   
68                   Bryan Mbeumo        Brentford        49.196225   
192                James Maddison        Tottenham        50.971203   
202                  Jarrod Bowen         West Ham        49.134280   
360                   Pascal Groß         Brighton        43.654466   
294               Martin Ødegaard          Arsenal        47.226310   
247                  Kaoru Mitoma         Brighton        44.091225   
370               Raheem Sterling          Chelsea        47.061547   
366                    Phil Foden  Manchester City        43.846884   
65         Bruno Borges Fernandes   Manchester Utd        44.499562   
198             James Ward-Prowse         West Ham        42.314325   
326                  Moussa Diaby      Aston Villa        42.424352   
290               Marcus Rashford   Manchester Utd        43.583564   
121  Douglas Luiz Soares de Paulo      Aston Villa        40.076720   
5              Abdoulaye Doucouré          Everton        38.623629   
123                  Eberechi Eze   Crystal Palace        39.242094   
410                   Solly March         Brighton        39.665066   
119            Dominik Szoboszlai        Liverpool        41.332352   

     expected_points_with_decay  number_of_games position  price  \
322                   10.014471               10      MID   12.9   
69                     8.783742               10      MID    8.6   
162                    9.037080               10      MID    9.6   
68                     7.817236                9      MID    6.7   
192                    7.859116               10      MID    8.1   
202                    7.633065               10      MID    7.4   
360                    6.880755               10      MID    6.3   
294                    7.276201               10      MID    8.5   
247                    6.942313               10      MID    6.5   
370                    6.951865               10      MID    6.9   
366                    6.928091                9      MID    7.5   
65                     7.007382               10      MID    8.3   
198                    6.595225               10      MID    6.2   
326                    6.609784               10      MID    6.8   
290                    6.880385               10      MID    8.7   
121                    6.231878               10      MID    5.6   
5                      6.026528               10      MID    5.5   
123                    6.250770               10      MID    6.2   
410                    6.236619               10      MID    6.3   
119                    6.504144               10      MID    7.1   

     dream_team_appearances  
322                   0.954  
69                    0.848  
162                   0.836  
68                    0.482  
192                   0.422  
202                   0.364  
360                   0.146  
294                   0.146  
247                   0.140  
370                   0.120  
366                   0.076  
65                    0.076  
198                   0.072  
326                   0.058  
290                   0.050  
121                   0.030  
5                     0.028  
123                   0.024  
410                   0.022  
119                   0.016

In [16]:
print('FORWARDS')
display(my_df
        .drop(['team', 'expected_points_with_noise_with_decay'], axis=1)
        [my_df['position']=='FWD']
        .sort_values(by='dream_team_appearances', ascending=False)
        .head(20))

FORWARDS


name          team_name  expected_points  \
353                     Ollie Watkins        Aston Villa        52.907381   
72                      Callum Wilson      Newcastle Utd        45.361440   
17                     Alexander Isak      Newcastle Utd        42.881278   
240                    Julián Álvarez    Manchester City        40.480384   
104              Darwin Núñez Ribeiro          Liverpool        41.565175   
134                    Erling Haaland    Manchester City        48.159283   
455                       Yoane Wissa          Brentford        35.828415   
124                     Eddie Nketiah            Arsenal        34.367316   
118                   Dominic Solanke        Bournemouth        36.186888   
91                         Cody Gakpo          Liverpool        36.054904   
301  Matheus Santos Carneiro Da Cunha             Wolves        33.149352   
117             Dominic Calvert-Lewin            Everton        34.513944   
340                   Nicolas Jackson            Chelsea        36.929986   
348                   Odsonne Edouard     Crystal Palace        30.041087   
414                     Taiwo Awoniyi  Nottingham Forest        30.466402   
13                Aleksandar Mitrović             Fulham        30.995522   
372                    Rasmus Højlund     Manchester Utd        29.820747   
136                     Evan Ferguson           Brighton        29.796420   
78                     Carlton Morris              Luton        30.008441   
314                   Michail Antonio           West Ham        31.283758   

     expected_points_with_decay  number_of_games position  price  \
353                    8.192552               10      FWD    8.4   
72                     6.977332               10      FWD    7.8   
17                     6.632418               10      FWD    7.5   
240                    6.412950                9      FWD    7.2   
104                    6.516042               10      FWD    7.5   
134                    7.650884                9      FWD   14.0   
455                    5.648388                9      FWD    5.9   
124                    5.294848               10      FWD    5.6   
118                    5.484125               10      FWD    6.4   
91                     5.675277               10      FWD    7.2   
301                    5.266923               10      FWD    5.5   
117                    5.380488               10      FWD    5.8   
340                    5.485603               10      FWD    6.8   
348                    4.801327               10      FWD    5.5   
414                    4.725424               10      FWD    6.4   
13                     4.770359               10      FWD    7.5   
372                    4.698805               10      FWD    7.1   
136                    4.694633               10      FWD    6.0   
78                     4.564123               10      FWD    5.4   
314                    4.893706               10      FWD    5.8   

     dream_team_appearances  
353                   0.864  
72                    0.348  
17                    0.182  
240                   0.142  
104                   0.132  
134                   0.060  
455                   0.030  
124                   0.022  
118                   0.020  
91                    0.012  
301                   0.012  
117                   0.010  
340                   0.010  
348                   0.006  
414                   0.006  
13                    0.004  
372                   0.002  
136                   0.002  
78                    0.002  
314                   0.002

In [17]:
players = optimize(my_df, max_price, 'dream_team_appearances', captain_double_points=False)

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/b9a15230d99c4aeba9103c9def5276df-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/b9a15230d99c4aeba9103c9def5276df-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 491 COLUMNS
At line 5865 RHS
At line 6352 BOUNDS
At line 7267 ENDATA
Problem MODEL has 486 rows, 914 columns and 3414 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 6.21 - 0.00 seconds
Cgl0004I processed model has 484 rows, 914 columns (914 integer (914 of which binary)) and 3199 elements
Cutoff increment increased from 1e-05 to 0.001998
Cbc0038I Initial state - 0 integers unsatisfied s

position                    name           team  price  \
20        GK   Alisson Ramses Becker      Liverpool    5.6   
253      DEF         Kieran Trippier  Newcastle Utd    7.0   
307      DEF              Matty Cash    Aston Villa    5.2   
365      DEF        Pervis Estupiñán       Brighton    5.3   
434      DEF  Trent Alexander-Arnold      Liverpool    7.9   
162      MID           Heung-Min Son      Tottenham    9.6   
202      MID            Jarrod Bowen       West Ham    7.4   
322      MID           Mohamed Salah      Liverpool   12.9   
68       MID            Bryan Mbeumo      Brentford    6.7   
69       MID             Bukayo Saka        Arsenal    8.6   
353      FWD           Ollie Watkins    Aston Villa    8.4   

     dream_team_appearances  
20                    0.174  
253                   0.654  
307                   0.150  
365                   0.166  
434                   0.718  
162                   0.836  
202                   0.364  
322                   0.954  
68                    0.482  
69                    0.848  
353                   0.864

In [ ]:
projections[(projections.gameweek==(latest_gameweek+1))].sort_values('expected_points', ascending=False)[['name', 'expected_points']].head(20)

In [ ]:
display(projections[projections.name.str.contains('Saliba')][['name', 'expected_points']])
display(projections[projections.name.str.contains('Saliba')][['expected_points_with_decay']].sum())